In [8]:
from gensim.test.utils import common_texts
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
from sklearn.metrics import accuracy_score, f1_score
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn import utils
import csv
from tqdm import tqdm
import multiprocessing
import nltk
from nltk.corpus import stopwords
import pandas as pd

In [12]:
#tqdm.pandas(desc="progress-bar")
# Function for tokenizing
def tokenize_text(text):
    tokens = []
    for sent in nltk.sent_tokenize(text):
        for word in nltk.word_tokenize(sent):
            if len(word) < 2:
                continue
            tokens.append(word.lower())
    return tokens
# Initializing the variables
train_documents = []
test_documents = []
i = 0
# Associating the tags(labels) with numbers
tags_index = {'sci-fi': 1 , 'action': 2, 'comedy': 3, 'fantasy': 4, 'animation': 5, 'romance': 6}
#Reading the file
FILEPATH = '../Datasets/tagged_plots_movielens.csv'
with open(FILEPATH, 'r') as csvfile:
    with open('../Datasets/tagged_plots_movielens.csv', 'r') as csvfile:
        moviereader = csv.reader(csvfile, delimiter=',', quotechar='"')
        for row in moviereader:
            if i == 0:
                i += 1
                continue
            i += 1
            if i <= 2000:
                train_documents.append(          TaggedDocument(words=tokenize_text(row[2]), tags=[tags_index.get(row[3], 8)] ))
            else:
                test_documents.append( TaggedDocument(words=tokenize_text(row[2]),
     tags=[tags_index.get(row[3], 8)]))
    print(train_documents[0])

TaggedDocument(['little', 'boy', 'named', 'andy', 'loves', 'to', 'be', 'in', 'his', 'room', 'playing', 'with', 'his', 'toys', 'especially', 'his', 'doll', 'named', '``', 'woody', "''", 'but', 'what', 'do', 'the', 'toys', 'do', 'when', 'andy', 'is', 'not', 'with', 'them', 'they', 'come', 'to', 'life', 'woody', 'believes', 'that', 'he', 'has', 'life', 'as', 'toy', 'good', 'however', 'he', 'must', 'worry', 'about', 'andy', "'s", 'family', 'moving', 'and', 'what', 'woody', 'does', 'not', 'know', 'is', 'about', 'andy', "'s", 'birthday', 'party', 'woody', 'does', 'not', 'realize', 'that', 'andy', "'s", 'mother', 'gave', 'him', 'an', 'action', 'figure', 'known', 'as', 'buzz', 'lightyear', 'who', 'does', 'not', 'believe', 'that', 'he', 'is', 'toy', 'and', 'quickly', 'becomes', 'andy', "'s", 'new', 'favorite', 'toy', 'woody', 'who', 'is', 'now', 'consumed', 'with', 'jealousy', 'tries', 'to', 'get', 'rid', 'of', 'buzz', 'then', 'both', 'woody', 'and', 'buzz', 'are', 'now', 'lost', 'they', 'must'

In [17]:
cores = multiprocessing.cpu_count()-1

model_dbow = Doc2Vec(dm=1, vector_size=300, negative=5, hs=0, min_count=2, sample = 0, workers=cores, alpha=0.025, min_alpha=0.001)
model_dbow.build_vocab([x for x in tqdm(train_documents)])
train_documents  = utils.shuffle(train_documents)
model_dbow.train(train_documents,total_examples=len(train_documents), epochs=30)
def vector_for_learning(model, input_docs):
    sents = input_docs
    targets, feature_vectors = zip(*[(doc.tags[0], model.infer_vector(doc.words, steps=20)) for doc in sents])
    return targets, feature_vectors
model_dbow.save('./movieModel.d2v')

100%|█████████████████████████████████████████████████████████████████████████| 1999/1999 [00:00<00:00, 2002965.53it/s]


In [15]:
cores = multiprocessing.cpu_count()-1

In [16]:
cores

3

In [18]:
y_train, X_train = vector_for_learning(model_dbow, train_documents)
y_test, X_test = vector_for_learning(model_dbow, test_documents)

logreg = LogisticRegression(n_jobs=1, C=1e5)
logreg.fit(X_train, y_train)
y_pred = logreg.predict(X_test)
print('Testing accuracy for movie plots%s' % accuracy_score(y_test, y_pred))
print('Testing F1 score for movie plots: {}'.format(f1_score(y_test, y_pred, average='weighted')))

c:\users\kavin\appdata\local\programs\python\python37\lib\site-packages\sklearn\linear_model\_logistic.py:939: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html.
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  extra_warning_msg=_LOGISTIC_SOLVER_CONVERGENCE_MSG)


Testing accuracy for movie plots0.41648106904231624
Testing F1 score for movie plots: 0.4118352114649635


In [20]:
X_train

(array([ 0.03525696,  0.30807912,  0.5557753 , -0.37150705,  0.13831605,
        -0.21833806, -0.2181245 ,  0.64728874,  0.4415637 , -0.0062982 ,
         0.05032701, -0.07186481,  0.02049766,  0.4312639 ,  0.09630775,
         0.08029863, -0.5346555 , -0.5679144 ,  0.37395814, -0.29637143,
        -0.18745399, -0.14147818, -0.2179708 ,  0.66706276,  0.22325711,
        -0.24178782,  0.15258051, -0.00643347,  0.08346221, -0.09735057,
        -0.08699938,  0.11112733,  0.40614507,  0.39993268, -0.09749555,
         0.04187145, -0.03689004,  0.05782603, -0.17281446,  0.10803916,
         0.02093272, -0.45691988, -0.49477282,  0.19863841, -0.22024064,
        -0.22138415,  0.49323043,  0.25131425, -0.0864789 , -0.71075404,
         0.34372574, -0.24603958,  0.27935058,  0.725393  ,  0.34823623,
        -0.8182867 ,  0.574936  , -0.205339  , -0.18647002, -0.27561134,
        -0.05452287,  0.37031186,  0.24420258, -0.31210893,  0.19438264,
         0.0665603 ,  0.2195199 ,  0.4097632 ,  0.1